# Silvae / Agroparistech Data

- Accessed latest on 2023-12-08: https://silvae.agroparistech.fr/home/?page_id=2683


## Libraries


In [1]:
# Magic
%load_ext autoreload
%autoreload 2

from tqdm import tqdm
import rasterio
from rasterio import windows

import pandas as pd
import glob
import numpy as np
import os
import chime
import matplotlib.pyplot as plt
from pyprojroot import here

chime.theme("mario")

# Import Functions
import sys

sys.path.insert(0, "../../src")
from run_mp import *
from utilities import *

In [2]:
# Clean where NA value is present, based on files' NA value
def clean_na_in_agroparistech(df_mp, df_vars):
    for col in df_mp.drop(columns=["idp", "x_fr", "y_fr"], errors="ignore").columns:
        # print(col)

        if col not in df_vars["variables"].values:
            print("❌❌❌ Column: ", col, " not in variables")
            continue
        current_na = df_vars.query("variables == @col")["na_value"].iloc[0]
        print("For column: ", col, "NA value is: ", current_na)

        for j in range(df_mp.shape[0]):
            if df_mp.at[j, col] == current_na:
                df_mp.at[j, col] = np.nan
    return df_mp

In [3]:
def get_file_size(filename):
    """Get file size in megabytes."""
    return os.path.getsize(filename) / (1024 * 1024)


def calculate_splits(file_size, max_mb):
    """Calculate the number of splits based on file size and maximum MB per split."""
    return max(1, int(file_size / max_mb))


def get_splits(height, num_splits):
    """Calculate window positions for splitting the raster with overlap."""
    split_height = height // num_splits
    overlap = int(split_height * 0.50)  # 10% overlap

    for i in range(num_splits):
        start = max(0, i * split_height - overlap)
        end = (
            min(height, (i + 1) * split_height + overlap)
            if i < num_splits - 1
            else height
        )
        yield (start, end - start)


def split_raster(input_raster, subfolder, max_mb):
    """Split a raster into subfiles based on maximum MB per file."""

    # Check file size and calculate number of splits
    file_size = get_file_size(input_raster)
    num_splits = calculate_splits(file_size, max_mb)

    # Create subfolder if it doesn't exist
    ffolder = f"{subfolder}/subrasters"
    if not os.path.exists(ffolder):
        os.makedirs(ffolder)

    # Get filename in short
    my_filename = input_raster.split("/")[-1].split(".")[0]

    print(f"Splitting {my_filename} into {num_splits} subfiles:")

    with rasterio.open(input_raster) as dataset:
        width = dataset.width
        height = dataset.height

        # Get list of subrasters
        f_subrasters = []

        for i, (start, split_height) in enumerate(get_splits(height, num_splits)):
            window = windows.Window(0, start, width, split_height)
            transform = dataset.window_transform(window)

            profile = dataset.profile
            profile.update(
                {"height": window.height, "width": window.width, "transform": transform}
            )

            # Get filename
            f_subraster = f"{ffolder}/{my_filename}_subraster_{i}.tif"

            # Write raster
            with rasterio.open(
                f_subraster,
                "w",
                **profile,
            ) as dst:
                dst.write(dataset.read(window=window))

            # Attach filename to list
            f_subrasters.append(f_subraster)

    return f_subrasters

# 👉 User Input


In [15]:
# For subsetting
take_subset = False
subset_size = 1000

# For file selection
run_fast_files = True

# For raster checks:
skip_raster_checks = True  # Directly load the raster info from the csv files
make_figures = False  # Takes 4 mins with plotting and 1.30 mins without

## Load Coordinates

- Note that both, the coordinates and the .tif files are in the same CRS (EPSG:2154), so we can use the coordinates directly for extracting the data from the .tif files.


In [16]:
# Get site coordinates
site_coordinates = get_final_nfi_coordinates("noisy", "csv")

# Take subset if needed
if take_subset:
    site_coordinates = site_coordinates.sample(subset_size, random_state=1)

# Define final df that will hold all data
df_coords = site_coordinates[["idp", "x_fr", "y_fr"]]
display(df_coords[:3])
df_coords.shape

Loading noisy coordinates from csv.


idp           x_fr          y_fr
0  500008  928612.835812  6.776642e+06
1  500013  563901.539379  6.901657e+06
2  500098  835978.113254  6.343803e+06

(41296, 3)

# Load Raster Files


In [17]:
# List all tiff files in agroparistech folder
files = sorted(glob.glob("../../data/raw/agroparistech/all_files/*.tif"))
files_ = [f.split("/")[-1] for f in files]
for i in range(len(files_)):
    print(f" {i}: {files_[i]}")

 0: abal_distrib_v2016.tif
 1: abal_mortalite_v2018.tif
 2: acca_distrib_v2016.tif
 3: acca_mortalite_v2018.tif
 4: acmo_distrib_v2016.tif
 5: acop_distrib_v2016.tif
 6: acpl_distrib_v2016.tif
 7: acps_distrib_v2016.tif
 8: algl_distrib_v2016.tif
 9: bepe_distrib_v2016.tif
 10: bepe_mortalite_v2018.tif
 11: bepu_distrib_v2016.tif
 12: bhctu_6190_an_v1.tif
 13: bhctu_6190_et_v1.tif
 14: cabe_distrib_v2016.tif
 15: cabe_mortalite_v2018.tif
 16: cas_59cl.tif
 17: casa_distrib_v2016.tif
 18: coav_mortalite_v2018.tif
 19: et_2014.tif
 20: etp_6190_an_v1.tif
 21: etp_6190_et_v1.tif
 22: fasy_distrib_v2016.tif
 23: fasy_if_v2018.tif
 24: fasy_mortalite_v2018.tif
 25: fran_distrib_v2016.tif
 26: frex_distrib_v2016.tif
 27: laan_mortalite_v2018.tif
 28: lade_mortalite_v2018.tif
 29: masy_mortalite_v2018.tif
 30: ph_2008.tif
 31: piab_distrib_v2016.tif
 32: piab_if_v2018.tif
 33: piab_mortalite_v2018.tif
 34: piha_distrib_v2016.tif
 35: pipi_mortalite_v2018.tif
 36: pisi_mortalite_v2018.tif
 37:

In [18]:
# Extract variables names from files
variables = [file.split("/")[-1].split(".")[0] for file in files]
variables[:3]

['abal_distrib_v2016', 'abal_mortalite_v2018', 'acca_distrib_v2016']

In [19]:
# Merge files and variables
files_variables = pd.DataFrame({"files": files, "variables": variables})
files_variables

files             variables
0   ../../data/raw/agroparistech/all_files/abal_di...    abal_distrib_v2016
1   ../../data/raw/agroparistech/all_files/abal_mo...  abal_mortalite_v2018
2   ../../data/raw/agroparistech/all_files/acca_di...    acca_distrib_v2016
3   ../../data/raw/agroparistech/all_files/acca_mo...  acca_mortalite_v2018
4   ../../data/raw/agroparistech/all_files/acmo_di...    acmo_distrib_v2016
..                                                ...                   ...
88  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_13
89  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_et
90  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_hi
91  ../../data/raw/agroparistech/all_files/ulgl_di...    ulgl_distrib_v2016
92  ../../data/raw/agroparistech/all_files/ulmi_di...    ulmi_distrib_v2016

[93 rows x 2 columns]

## Attach Raster Information


In [20]:
# Loop through all files, open the raster, save an image of it, and attach the crs to the df

if not skip_raster_checks:
    for i in tqdm(range(files_variables.shape[0]), disable=False):
        # print(f" {i}. Working on {files_variables['variables'].iloc[i]}...")

        # Open raster
        raster = rasterio.open(files_variables["files"].iloc[i])

        # Load Image
        image = raster.read(1)

        # Turn into float to avoid error when putting values to NA
        image = image.astype(float)  # Convert to float

        # Get min value and CRS
        my_crs = raster.crs.to_string()
        my_na = np.min(image)

        # Attach CRS and min value to df
        files_variables = files_variables.copy()
        files_variables.at[i, "crs"] = my_crs
        files_variables.at[i, "na_value"] = my_na

        if make_figures:
            # Plot
            # Set minimum value to na
            image[image == np.min(image)] = np.nan
            # Add caption with the CRS and min value
            plt.figure(figsize=(8, 8))
            plt.imshow(image)
            plt.colorbar(fraction=0.046, pad=0.04)
            plt.title(f"{files_variables['variables'].iloc[i]}")
            plt.text(
                0,
                1300,
                f"Min Value: {my_na}\nCRS: {my_crs[:50]}...",
            )
            plt.savefig(
                f"agroparistech_qc_files/raster_{files_variables['variables'].iloc[i]}.png"
            )
            # plt.show()
            plt.close()

    # Check df
    display(files_variables.head(3))

    # Replace CRS with EPSG code
    for i in tqdm(range(files_variables.shape[0]), disable=False):
        if "RGF_1993_Lambert_Conformal" in files_variables["crs"].iloc[i]:
            files_variables.at[i, "crs"] = "EPSG:2154"

    display(files_variables.value_counts("crs"))

    # Save file
    files_variables.to_csv("agroparistech_qc_files/files_variables.csv", index=False)
    display(files_variables)
else:
    files_variables = pd.read_csv("agroparistech_qc_files/files_variables.csv")
    display(files_variables)

files             variables  \
0   ../../data/raw/agroparistech/all_files/abal_di...    abal_distrib_v2016   
1   ../../data/raw/agroparistech/all_files/abal_mo...  abal_mortalite_v2018   
2   ../../data/raw/agroparistech/all_files/acca_di...    acca_distrib_v2016   
3   ../../data/raw/agroparistech/all_files/acca_mo...  acca_mortalite_v2018   
4   ../../data/raw/agroparistech/all_files/acmo_di...    acmo_distrib_v2016   
..                                                ...                   ...   
88  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_13   
89  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_et   
90  ../../data/raw/agroparistech/all_files/tx61858...         tx61858610_hi   
91  ../../data/raw/agroparistech/all_files/ulgl_di...    ulgl_distrib_v2016   
92  ../../data/raw/agroparistech/all_files/ulmi_di...    ulmi_distrib_v2016   

          crs      na_value  
0   EPSG:2154 -3.402823e+38  
1   EPSG:2154 -9.999000e+03  
2   EPSG:2154 -3.402823e+38  
3   EPSG:2154 -9.999000e+03  
4   EPSG:2154 -3.402823e+38  
..        ...           ...  
88  EPSG:2154 -3.402823e+38  
89  EPSG:2154 -3.402823e+38  
90  EPSG:2154 -3.402823e+38  
91  EPSG:2154 -3.402823e+38  
92  EPSG:2154 -3.402823e+38  

[93 rows x 4 columns]

### Split fast and slow files


In [21]:
# These files are too big and take very long to extract
# So skipping them for now and will extract them separately
skip_these_files = [
    "tmoy_6190_et_v1",
    "tmoy_6190_hi_v1",
    "tmoy_6190_an_v1",
    "tmin_6190_hi_v1",
    "tmax_6190_et_v1",
    "rad_6190_et_v1",
    "rad_6190_an_v1",
    "etp_6190_et_v1",
    "etp_6190_an_v1",
    "bhctu_6190_et_v1",
    "bhctu_6190_an_v1",
    "ru_6190_et_v1",
    "ru_6190_an_v1",
]

files_variables_quick = files_variables[
    ~files_variables["variables"].isin(skip_these_files)
].reset_index(drop=True)

files_variables_slow = files_variables[
    files_variables["variables"].isin(skip_these_files)
].reset_index(drop=True)

print(f"Shape of files_variables_quick: {files_variables_quick.shape}")
for i in range(files_variables_quick.shape[0]):
    print(
        f" {i}. {files_variables_quick['variables'].iloc[i]:<20}\t{files_variables_quick['files'].iloc[i]}"
    )

display(f"Shape of files_variables_slow: {files_variables_slow.shape}")
for i in range(files_variables_slow.shape[0]):
    print(
        f" {i}. {files_variables_slow['variables'].iloc[i]:<20}\t{files_variables_slow['files'].iloc[i]}"
    )

Shape of files_variables_quick: (80, 4)
 0. abal_distrib_v2016  	../../data/raw/agroparistech/all_files/abal_distrib_v2016.tif
 1. abal_mortalite_v2018	../../data/raw/agroparistech/all_files/abal_mortalite_v2018.tif
 2. acca_distrib_v2016  	../../data/raw/agroparistech/all_files/acca_distrib_v2016.tif
 3. acca_mortalite_v2018	../../data/raw/agroparistech/all_files/acca_mortalite_v2018.tif
 4. acmo_distrib_v2016  	../../data/raw/agroparistech/all_files/acmo_distrib_v2016.tif
 5. acop_distrib_v2016  	../../data/raw/agroparistech/all_files/acop_distrib_v2016.tif
 6. acpl_distrib_v2016  	../../data/raw/agroparistech/all_files/acpl_distrib_v2016.tif
 7. acps_distrib_v2016  	../../data/raw/agroparistech/all_files/acps_distrib_v2016.tif
 8. algl_distrib_v2016  	../../data/raw/agroparistech/all_files/algl_distrib_v2016.tif
 9. bepe_distrib_v2016  	../../data/raw/agroparistech/all_files/bepe_distrib_v2016.tif
 10. bepe_mortalite_v2018	../../data/raw/agroparistech/all_files/bepe_mortalite_v2018.

'Shape of files_variables_slow: (13, 4)'

 0. bhctu_6190_an_v1    	../../data/raw/agroparistech/all_files/bhctu_6190_an_v1.tif
 1. bhctu_6190_et_v1    	../../data/raw/agroparistech/all_files/bhctu_6190_et_v1.tif
 2. etp_6190_an_v1      	../../data/raw/agroparistech/all_files/etp_6190_an_v1.tif
 3. etp_6190_et_v1      	../../data/raw/agroparistech/all_files/etp_6190_et_v1.tif
 4. rad_6190_an_v1      	../../data/raw/agroparistech/all_files/rad_6190_an_v1.tif
 5. rad_6190_et_v1      	../../data/raw/agroparistech/all_files/rad_6190_et_v1.tif
 6. ru_6190_an_v1       	../../data/raw/agroparistech/all_files/ru_6190_an_v1.tif
 7. ru_6190_et_v1       	../../data/raw/agroparistech/all_files/ru_6190_et_v1.tif
 8. tmax_6190_et_v1     	../../data/raw/agroparistech/all_files/tmax_6190_et_v1.tif
 9. tmin_6190_hi_v1     	../../data/raw/agroparistech/all_files/tmin_6190_hi_v1.tif
 10. tmoy_6190_an_v1     	../../data/raw/agroparistech/all_files/tmoy_6190_an_v1.tif
 11. tmoy_6190_et_v1     	../../data/raw/agroparistech/all_files/tmoy_6190_et_v1.

### Fast Files


In [22]:
if run_fast_files:
    # Add groupings, make sure that slow variables are split to own cores
    files_variables_quick = files_variables_quick.copy()
    files_variables_quick["group"] = np.arange(len(files_variables_quick)) % 10 + 1

    # Create list of df to be passed to multiprocessing
    grouped = files_variables_quick.groupby("group")
    df_list = [group for name, group in grouped]

    # Display one group
    df_list[0].head(3)

In [23]:
if run_fast_files:
    pass
    # Test on one group
    # df_test = parallel_agroparistech_extraction(df_list[0], df_coords, progress_bar=False)
    # df_test = df_test.copy()

    # # Print shape
    # df_test.shape

    # # Replace NA values
    # df_test = clean_na_in_agroparistech(df_test, files_variables_quick)

    # # Final display
    # display(df_test.head(3))
    # display(df_test.tail(3))

In [24]:
# Takes about 7:00 mins to run
if run_fast_files:
    # Run in parallel
    df_quick = run_mp(
        parallel_agroparistech_extraction,
        df_list,
        progress_bar=True,
        num_cores=10,
        df_coords=df_coords,
        verbose=False,
    )

    # Combine the list of dataframes using list comprehension
    df_quick_merged = df_quick[0]
    for i in range(1, len(df_quick)):
        df_quick_merged = pd.merge(
            df_quick_merged, df_quick[i], on=["idp", "y_fr", "x_fr"], how="left"
        )

    # Replace faulty NA values
    df_quick_merged = clean_na_in_agroparistech(df_quick_merged, files_variables_quick)

    # Display final df
    display(df_quick_merged)

    # Notify me when done
    chime.success()

  0%|          | 0/10 [06:14<?, ?it/s]


In [179]:
if run_fast_files:
    # Cleaning df
    df_quick_merged = df_quick_merged.drop(
        columns=["x_fr", "y_fr"]
    )  # remove coordinates
    df_quick_merged = df_quick_merged.reindex(
        sorted(df_quick_merged.columns), axis=1
    )  # sort alphabetically
    df_quick_merged.insert(
        0, "idp", df_quick_merged.pop("idp")
    )  # move idp to first again

    print(f"Final columns in df_quick_merged:")
    for i in range(df_quick_merged.shape[1]):
        print(f" {i}. {df_quick_merged.columns[i]}")

In [184]:
if run_fast_files:
    # Save it
    if take_subset:
        df_quick_merged.to_feather(
            "data_agroparistech_fastfiles_before_qc_subset.feather"
        )
    else:
        df_quick_merged.to_feather("data_agroparistech_fastfiles_before_qc.feather")

    # Display it
    display(df_quick_merged)

else:
    # Load it
    if take_subset:
        filename = "data_agroparistech_fastfiles_before_qc_subset.feather"
    else:
        filename = "data_agroparistech_fastfiles_before_qc.feather"

    filectime = os.path.getctime(filename)
    filectime = pd.to_datetime(filectime, unit="s")
    pd.read_feather(filename)

    print(f"Loaded file from date: {filectime}")

    # Display it
    display(df_quick_merged)

Loaded file from date: 2023-12-12 18:58:23.521314816


idp  abal_distrib_v2016  abal_mortalite_v2018  acca_distrib_v2016  \
0       632691            0.116299              0.008844            0.000375   
1       702597            0.085622                   NaN            0.034614   
2       706240            0.051618                   NaN            0.115233   
3       708321            0.040013                   NaN            0.148194   
4       708369            0.000747                   NaN            0.005307   
...        ...                 ...                   ...                 ...   
40017  1131396            0.045600                   NaN            0.083468   
40018  1131409            0.473966              0.003952            0.001264   
40019  1131410            0.049305              0.005269            0.318085   
40020  1131424            0.607617              0.004181            0.002270   
40021  1131437            0.116348                   NaN            0.115151   

       acca_mortalite_v2018  acmo_distrib_v2016  acop_distrib_v2016  \
0                       NaN        9.924152e-07            0.000003   
1                       NaN        5.261347e-04            0.000139   
2                  0.004216        5.093967e-03            0.000398   
3                       NaN        1.956224e-02            0.001257   
4                       NaN        2.101506e-03            0.000395   
...                     ...                 ...                 ...   
40017              0.002775        4.144695e-03            0.000253   
40018                   NaN        3.350771e-05            0.002684   
40019              0.003344        1.996571e-02            0.004037   
40020                   NaN        2.319062e-05            0.001624   
40021                   NaN        1.644042e-03            0.000703   

       acpl_distrib_v2016  acps_distrib_v2016  algl_distrib_v2016  ...  \
0                0.000940            0.014346            0.172500  ...   
1                0.007517            0.083863            0.042155  ...   
2                0.009477            0.062689            0.031795  ...   
3                0.011965            0.051941            0.006399  ...   
4                0.000026            0.000055            0.011447  ...   
...                   ...                 ...                 ...  ...   
40017            0.008234            0.044094            0.033205  ...   
40018            0.006176            0.204999            0.001898  ...   
40019            0.028711            0.100558            0.006682  ...   
40020            0.012876            0.219644            0.006279  ...   
40021            0.012293            0.129440            0.021215  ...   

       tm61858610_et  tm61858610_hi  tn61858610_13  tn61858610_et  \
0           0.862332       0.654225       0.783792       0.781635   
1           1.373271       0.814091       1.083123       1.395909   
2           1.344592       0.734841       1.035151       1.326922   
3           1.172818       0.662550       0.775894       0.946536   
4           1.371573       0.495906       0.875836       1.327507   
...              ...            ...            ...            ...   
40017       1.265831       0.694509       0.897891       1.173905   
40018       1.229290       0.433623       0.814746       1.185932   
40019       1.104976       0.981008       0.965759       1.205385   
40020       1.310417       0.661020       0.930633       1.087019   
40021       1.337960       0.712006       0.988353       1.282079   

       tn61858610_hi  tx61858610_13  tx61858610_et  tx61858610_hi  \
0           0.702837       0.831903       0.962231       0.615751   
1           0.798151       0.990023       1.284485       0.754891   
2           0.781010       0.985128       1.290603       0.699888   
3           0.560707       1.048530       1.391778       0.732056   
4           0.326096       1.014589       1.372826       0.792326   
...              ...            ...            ...            ...

### Slow Files

- Data was extracted in QGIS!
- There is a batch profile file to use in `"qgis/agroparistech_extraction/extractions/"`
-
- The 13 files are labelled with red tags in `"data/raw/agroparistech/with_qgis/."`


In [ ]:
dir_slow_files = "../../qgis/agroparistech_extraction/extractions/"
list_slow_files = sorted(glob.glob(dir_slow_files + "*.csv"))

i = 0
for pattern in skip_these_files:
    i = i + 1
    # Check if any file in list_slow_files contains the pattern
    if any(pattern in file for file in list_slow_files):
        print(f" {i}. ✅ {pattern}\t is in list_slow_files")
    else:
        print(f" {i}. ❌ {pattern}\t is NOT in list_slow_files")

 - ✅ tmoy_6190_et_v1	 is in list_slow_files
 - ✅ tmoy_6190_hi_v1	 is in list_slow_files
 - ✅ tmoy_6190_an_v1	 is in list_slow_files
 - ✅ tmin_6190_hi_v1	 is in list_slow_files
 - ✅ tmax_6190_et_v1	 is in list_slow_files
 - ✅ rad_6190_et_v1	 is in list_slow_files
 - ✅ rad_6190_an_v1	 is in list_slow_files
 - ✅ etp_6190_et_v1	 is in list_slow_files
 - ✅ etp_6190_an_v1	 is in list_slow_files
 - ✅ bhctu_6190_et_v1	 is in list_slow_files
 - ✅ bhctu_6190_an_v1	 is in list_slow_files
 - ✅ ru_6190_et_v1	 is in list_slow_files
 - ✅ ru_6190_an_v1	 is in list_slow_files


In [205]:
# Load all csv files and merge them column wise on "idp"
dfs = []

for file in list_slow_files:
    df = pd.read_csv(file).drop(
        columns=["x_fr", "y_fr", "x", "y", "SiteID", "first_year"], errors="ignore"
    )
    dfs.append(df)

# Merge the dataframes column-wise on the "idp" column
df_slow = dfs[0]
for i in range(1, len(dfs)):
    df_slow = pd.merge(df_slow, dfs[i], on=["idp"], how="left")

# Clean up weird column names artifact of v11 -> v1
df_slow.columns = df_slow.columns.str.replace("_v11", "_v1")

# Display the merged dataframe
df_slow

idp  bhctu_6190_an_v1  bhctu_6190_et_v1  etp_6190_an_v1  \
0       632691         19.240328        -56.831585       54.696297   
1       702597          2.667820        -53.173649       59.746429   
2       706240          5.251337        -58.659328       59.844738   
3       708321         -0.896232        -65.469238       55.652546   
4       708369         -5.091545       -106.926773       77.560204   
...        ...               ...               ...             ...   
40017  1131396          5.499433        -60.084801       58.913837   
40018  1131409         37.150269        -38.758152       48.179234   
40019  1131410         -1.225190        -51.083538       56.722427   
40020  1131424         29.439064        -39.102612       48.235397   
40021  1131437         18.777222        -48.608757       55.328762   

       etp_6190_et_v1  rad_6190_an_v1  rad_6190_et_v1  ru_6190_an_v1  \
0          105.875206    34664.031250    61088.796875      87.727051   
1          121.191681    36479.175781    65196.480469      68.788803   
2          120.269440    35390.437500    63748.859375      82.321030   
3          111.108696    32837.777344    60114.699219      68.584763   
4          142.603653    45841.847656    73121.804688      38.445492   
...               ...             ...             ...            ...   
40017      117.905334    34357.707031    62402.144531      73.945518   
40018      110.915405    48351.375000    73728.343750      45.601910   
40019      117.782784    33834.363281    62307.417969      25.748646   
40020      113.498116    42118.585938    70955.203125      80.065598   
40021      115.030640    34257.363281    62869.097656      50.207844   

       ru_6190_et_v1  tmax_6190_et_v1  tmin_6190_hi_v1  tmoy_6190_an_v1  \
0          45.103413        20.201530         1.330506         9.794139   
1          36.356426        24.533415        -0.847523        10.189947   
2          41.134739        24.560297        -0.348177        10.624409   
3          26.241491        23.672544         0.540477        10.560602   
4           1.948985        27.886978         2.486555        13.884115   
...              ...              ...              ...              ...   
40017      32.590038        24.278337        -0.403354        10.768160   
40018      22.320688        16.900511        -4.971567         5.346755   
40019       3.261593        24.364176        -1.769274        10.052839   
40020      47.248837        19.609493        -4.309597         5.802639   
40021      19.152031        22.948914        -1.049967         9.539359   

       tmoy_6190_et_v1  tmoy_6190_hi_v1  
0            15.093793         4.842273  
1            17.529387         3.008466  
2            18.022928         3.403141  
3            17.185537         4.298682  
4            21.347033         7.025046  
...                ...              ...  
40017        18.004129         3.664252  
40018        11.862495        -0.202282  
40019        18.008896         1.936617  
40020        13.182920        -1.014067  
40021        16.781227         2.464245  

[40022 rows x 14 columns]

# Merge all data


In [213]:
df_merged = pd.merge(df_quick_merged, df_slow, on=["idp"], how="left")
display(df_merged)

idp  abal_distrib_v2016  abal_mortalite_v2018  acca_distrib_v2016  \
0       632691            0.116299              0.008844            0.000375   
1       702597            0.085622                   NaN            0.034614   
2       706240            0.051618                   NaN            0.115233   
3       708321            0.040013                   NaN            0.148194   
4       708369            0.000747                   NaN            0.005307   
...        ...                 ...                   ...                 ...   
40017  1131396            0.045600                   NaN            0.083468   
40018  1131409            0.473966              0.003952            0.001264   
40019  1131410            0.049305              0.005269            0.318085   
40020  1131424            0.607617              0.004181            0.002270   
40021  1131437            0.116348                   NaN            0.115151   

       acca_mortalite_v2018  acmo_distrib_v2016  acop_distrib_v2016  \
0                       NaN        9.924152e-07            0.000003   
1                       NaN        5.261347e-04            0.000139   
2                  0.004216        5.093967e-03            0.000398   
3                       NaN        1.956224e-02            0.001257   
4                       NaN        2.101506e-03            0.000395   
...                     ...                 ...                 ...   
40017              0.002775        4.144695e-03            0.000253   
40018                   NaN        3.350771e-05            0.002684   
40019              0.003344        1.996571e-02            0.004037   
40020                   NaN        2.319062e-05            0.001624   
40021                   NaN        1.644042e-03            0.000703   

       acpl_distrib_v2016  acps_distrib_v2016  algl_distrib_v2016  ...  \
0                0.000940            0.014346            0.172500  ...   
1                0.007517            0.083863            0.042155  ...   
2                0.009477            0.062689            0.031795  ...   
3                0.011965            0.051941            0.006399  ...   
4                0.000026            0.000055            0.011447  ...   
...                   ...                 ...                 ...  ...   
40017            0.008234            0.044094            0.033205  ...   
40018            0.006176            0.204999            0.001898  ...   
40019            0.028711            0.100558            0.006682  ...   
40020            0.012876            0.219644            0.006279  ...   
40021            0.012293            0.129440            0.021215  ...   

       etp_6190_et_v1  rad_6190_an_v1  rad_6190_et_v1  ru_6190_an_v1  \
0          105.875206    34664.031250    61088.796875      87.727051   
1          121.191681    36479.175781    65196.480469      68.788803   
2          120.269440    35390.437500    63748.859375      82.321030   
3          111.108696    32837.777344    60114.699219      68.584763   
4          142.603653    45841.847656    73121.804688      38.445492   
...               ...             ...             ...            ...   
40017      117.905334    34357.707031    62402.144531      73.945518   
40018      110.915405    48351.375000    73728.343750      45.601910   
40019      117.782784    33834.363281    62307.417969      25.748646   
40020      113.498116    42118.585938    70955.203125      80.065598   
40021      115.030640    34257.363281    62869.097656      50.207844   

       ru_6190_et_v1  tmax_6190_et_v1  tmin_6190_hi_v1  tmoy_6190_an_v1  \
0          45.103413        20.201530         1.330506         9.794139   
1          36.356426        24.533415        -0.847523        10.189947   
2          41.134739        24.560297        -0.348177        10.624409   
3          26.241491        23.672544         0.540477        10.560602   
4           1.948985        27.886978         2.486555        13.884

# Clean Final Data


In [220]:
var_file_dict = {
    "tmoy_6190_et_v1": "pa_mean_summer_temp_61_90",
    "tmoy_6190_hi_v1": "pa_mean_winter_temp_61_90",
    "tmoy_6190_an_v1": "pa_mean_annual_temp_61_90",
    "tmin_6190_hi_v1": "pa_min_winter_temp_61_90",
    "tmax_6190_et_v1": "pa_max_summer_temp_61_90",
    "rad_6190_et_v1": "pa_mean_summer_radi_61_90",
    "rad_6190_an_v1": "pa_mean_annual_radi_61_90",
    "prec_6190_et_v1": "pa_mean_summer_prec_61_90",
    "prec_6190_an_v1": "pa_mean_annual_prec_61_90",
    "etp_6190_et_v1": "pa_mean_summer_etp_61_90",
    "etp_6190_an_v1": "pa_mean_annual_etp_61_90",
    "bhctu_6190_et_v1": "pa_mean_summer_wb_61_90",
    "bhctu_6190_an_v1": "pa_mean_annual_wb_61_90",
    "tm61858610_et": "pa_cc_mean_summer_temp",
    "tm61858610_hi": "pa_cc_mean_winter_temp",
    "tm61858610_13": "pa_cc_mean_annual_temp",
    "tn61858610_et": "pa_cc_min_summer_temp",
    "tn61858610_hi": "pa_cc_min_winter_temp",
    "tn61858610_13": "pa_cc_min_annual_temp",
    "tx61858610_et": "pa_cc_max_summer_temp",
    "tx61858610_hi": "pa_cc_max_winter_temp",
    "tx61858610_13": "pa_cc_max_annual_temp",
    "rr61858610_et": "pa_cc_mean_summer_prec",
    "rr61858610_13": "pa_cc_mean_annual_prec",
    "ph_2008": "pa_soil_pH",
    "rum_500_v2009": "pa_soil_max_whc",
    "et_2014": "pa_soil_watterlog",
    "ru_6190_et_v1": "pa_soil_summer_whc",
    "ru_6190_an_v1": "pa_soil_annual_whc",
    "cas_59cl": "pa_stations",
    "abal_distrib_v2016": "pa_distr_abiesalba",
    "acca_distrib_v2016": "pa_distr_acercampestre",
    "acmo_distrib_v2016": "pa_distr_acermonspessulanum",
    "acop_distrib_v2016": "pa_distr_aceropalus",
    "acpl_distrib_v2016": "pa_distr_acerplatanoides",
    "acps_distrib_v2016": "pa_distr_acerpseudoplatanus",
    "algl_distrib_v2016": "pa_distr_alnusglutinosa",
    "bepe_distrib_v2016": "pa_distr_betulapendula",
    "bepu_distrib_v2016": "pa_distr_betulapubescens",
    "cabe_distrib_v2016": "pa_distr_carpinusbetulus",
    "casa_distrib_v2016": "pa_distr_castaneasativa",
    "fasy_distrib_v2016": "pa_distr_fagussylvatica",
    "fran_distrib_v2016": "pa_distr_fraxinusangustifolia",
    "frex_distrib_v2016": "pa_distr_fraxinusexcelsior",
    "piab_distrib_v2016": "pa_distr_piceaabies",
    "piha_distrib_v2016": "pa_distr_pinushalepensis",
    "pisy_distrib_v2016": "pa_distr_pinussylvestris",
    "prav_distrib_v2016": "pa_distr_prunusavium",
    "quil_distrib_v2016": "pa_distr_quercusilex",
    "qupe_distrib_v2016": "pa_distr_quercuspetraea",
    "qupu_distrib_v2016": "pa_distr_quercuspubescens",
    "quro_distrib_v2016": "pa_distr_quercusrobur",
    "rops_distrib_v2016": "pa_distr_robiniapseudoacacia",
    "saal_distrib_v2016": "pa_distr_salixalba",
    "saca_distrib_v2016": "pa_distr_salixcaprea",
    "saci_distrib_v2016": "pa_distr_salixcinerea",
    "soar_distrib_v2016": "pa_distr_sorbusaria",
    "soau_distrib_v2016": "pa_distr_sorbusaucuparia",
    "soto_distrib_v2016": "pa_distr_sorbustorminalis",
    "tico_distrib_v2016": "pa_distr_tiliacordata",
    "tipl_distrib_v2016": "pa_distr_tiliaplatyphyllos",
    "ulgl_distrib_v2016": "pa_distr_ulmusglabra",
    "ulmi_distrib_v2016": "pa_distr_ulmusminor",
    "fasy_if_v2018": "pa_growth_fagussylvatica",
    "piab_if_v2018": "pa_growth_piceaabies",
    "abal_vulnerabilite_vosges": "pa_mort_abiesalba",
    "piab_vulnerabilite_vosges": "pa_mort_abiesalba",
    "abal_mortalite_v2018": "pa_mort_abiesalba",
    "acca_mortalite_v2018": "pa_mort_acercampestre",
    "bepe_mortalite_v2018": "pa_mort_betulapendula",
    "cabe_mortalite_v2018": "pa_mort_carpinusbetulus",
    "coav_mortalite_v2018": "pa_mort_corylusavellana",
    "fasy_mortalite_v2018": "pa_mort_fagussylvatica",
    "laan_mortalite_v2018": "pa_mort_laburnumanagyroides",
    "lade_mortalite_v2018": "pa_mort_larixdecidua",
    "masy_mortalite_v2018": "pa_mort_malussylvestris",
    "piab_mortalite_v2018": "pa_mort_piceaabies",
    "pipi_mortalite_v2018": "pa_mort_pinuspinaster",
    "pisi_mortalite_v2018": "pa_mort_piceasitchensis",
    "pisy_mortalite_v2018": "pa_mort_pinussylvestris",
    "potr_mortalite_v2018": "pa_mort_populustremula",
    "prav_mortalite_v2018": "pa_mort_prunusavium",
    "psme_mortalite_v2018": "pa_mort_pseudotsugamenziesii",
    "quil_mortalite_v2018": "pa_mort_quercusilex",
    "qupe_mortalite_v2018": "pa_mort_quercuspetraea",
    "qupu_mortalite_v2018": "pa_mort_quercuspubescens",
    "qupy_mortalite_v2018": "pa_mort_quercuspyrenaica",
    "quro_mortalite_v2018": "pa_mort_quercusrobur",
    "rops_mortalite_v2018": "pa_mort_robiniapseudoacacia",
    "saal_mortalite_v2018": "pa_mort_salixalba",
    "saca_mortalite_v2018": "pa_mort_salixcaprea",
    "soau_mortalite_v2018": "pa_mort_sorbusaucuparia",
    "soto_mortalite_v2018": "pa_mort_sorbustorminalis",
}

In [219]:
# Replace NA values as indicated in the tiff files
df_merged_clean = clean_na_in_agroparistech(df_merged, files_variables)

For column:  abal_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  abal_mortalite_v2018 NA value is:  -9999.0
For column:  acca_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  acca_mortalite_v2018 NA value is:  -9999.0
For column:  acmo_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  acop_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  acpl_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  acps_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  algl_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  bepe_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  bepe_mortalite_v2018 NA value is:  -9999.0
For column:  bepu_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  cabe_distrib_v2016 NA value is:  -3.4028230607370965e+38
For column:  cabe_mortalite_v2018 NA value is:  -9999.0
For column:  cas_59cl NA value is:  -3.0
For column:  casa_distrib_v2016 NA 

In [221]:
# For variables with "distr" in their name, replace all values below 1e-6 with 0 (senseless values)
for col in df_merged_clean.columns:
    if "distr" in col:
        df_merged_clean[col] = df_merged_clean[col].apply(
            lambda x: x if x > 1e-6 else 0
        )

In [222]:
# Rename all columns to their original names
df_merged_clean = df_merged_clean.rename(columns=var_file_dict)

In [224]:
df_merged_clean

idp  pa_distr_abiesalba  pa_mort_abiesalba  pa_distr_acercampestre  \
0       632691            0.116299           0.008844                0.000375   
1       702597            0.085622                NaN                0.034614   
2       706240            0.051618                NaN                0.115233   
3       708321            0.040013                NaN                0.148194   
4       708369            0.000747                NaN                0.005307   
...        ...                 ...                ...                     ...   
40017  1131396            0.045600                NaN                0.083468   
40018  1131409            0.473966           0.003952                0.001264   
40019  1131410            0.049305           0.005269                0.318085   
40020  1131424            0.607617           0.004181                0.002270   
40021  1131437            0.116348                NaN                0.115151   

       pa_mort_acercampestre  pa_distr_acermonspessulanum  \
0                        NaN                     0.000000   
1                        NaN                     0.000526   
2                   0.004216                     0.005094   
3                        NaN                     0.019562   
4                        NaN                     0.002102   
...                      ...                          ...   
40017               0.002775                     0.004145   
40018                    NaN                     0.000000   
40019               0.003344                     0.019966   
40020                    NaN                     0.000000   
40021                    NaN                     0.001644   

       pa_distr_aceropalus  pa_distr_acerplatanoides  \
0                 0.000000                  0.000940   
1                 0.000139                  0.007517   
2                 0.000398                  0.009477   
3                 0.001257                  0.011965   
4                 0.000395                  0.000000   
...                    ...                       ...   
40017             0.000253                  0.008234   
40018             0.002684                  0.006176   
40019             0.004037                  0.028711   
40020             0.001624                  0.012876   
40021             0.000703                  0.012293   

       pa_distr_acerpseudoplatanus  pa_distr_alnusglutinosa  ...  \
0                         0.014346                 0.172500  ...   
1                         0.083863                 0.042155  ...   
2                         0.062689                 0.031795  ...   
3                         0.051941                 0.006399  ...   
4                         0.000000                 0.011447  ...   
...                            ...                      ...  ...   
40017                     0.044094                 0.033205  ...   
40018                     0.204999                 0.001898  ...   
40019                     0.100558                 0.006682  ...   
40020                     0.219644                 0.006279  ...   
40021                     0.129440                 0.021215  ...   

       pa_mean_summer_etp_61_90  pa_mean_annual_radi_61_90  \
0                    105.875206               34664.031250   
1                    121.191681               36479.175781   
2                    120.269440               35390.437500   
3                    111.108696               32837.777344   
4                    142.603653               45841.847656   
...                         ...                        ...   
40017                117.905334               34357.707031   
40018                110.915405               48351.375000   
40019                117.782784               33834.363281   
40020                113.498116               42118.585938   
40021                115.030640               34257.363281   

       pa_mean_summer_radi_61_90  pa_soil_annual_whc  pa_soil_summer_w

# Create Report


In [223]:
from ydata_profiling import ProfileReport

report = ProfileReport(
    df_merged_clean, title="Agroparistech Extraction Report", minimal=True
)
report.to_file("report_agroparistech_final_data.html")
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

# Save Data


In [225]:
df_merged_clean.to_feather("data_agroparistech_all.feather")
chime.success()